In [1]:
import ROOT

in_file = ROOT.TFile("~/work/sti-profiling/inputs_joinTwo.root")
#in_file = ROOT.TFile("/home/smirnovd/my-tests-data/inputs_joinTwo.root")

t = in_file.Get("t")

ROOT.enableJSVis()
ROOT.gStyle.SetPadRightMargin(0.3)

Welcome to JupyROOT 6.10/02


In [2]:
import plotly
import plotly.figure_factory as ff
import plotly.graph_objs as go

plotly.offline.init_notebook_mode(connected=True)

In [3]:
# Define some functions

g_h_counter = 1

# Fill 1D histogram from the tree
def project1D(expression, x_bins, x_first, x_last, h_title = "", selection = ""):

    global g_h_counter

    h_name = 'h_{:03d}'.format(g_h_counter)
    g_h_counter += 1

    if h_title == "":
        h_title = expression

    h1D = ROOT.TH1D(h_name, h_title, x_bins, x_first, x_last)

    t.Project(h_name, expression, selection)

    return h1D



# Fill 2D histogram from the tree
def project2D(expression, x_bins, x_first, x_last, y_bins, y_first, y_last,
              h_title = "", selection = "", draw_options = ""):

    global g_h_counter

    h_name = 'h_{:03d}'.format(g_h_counter)
    g_h_counter += 1

    if h_title == "":
        h_title = expression

    h2D = ROOT.TH2D(h_name, h_title, x_bins, x_first, x_last, y_bins, y_first, y_last)
    h2D.SetOption(draw_options)

    t.Project(h_name, expression, selection, draw_options)

    return h2D



def drawOnCanvases(hists, width = 800, height = 600):

    canvases = []

    for hist in hists:
        canvas = ROOT.TCanvas("canvas_" + hist.GetName(), "ROOT Canvas", width, height)
        hist.Draw( hist.GetOption() )
        canvas.Draw()
        canvases.append(canvas)

    return canvases



def getCumulative(hists):

    hists_cumul = []

    for hist in hists:
        hist_cumul = hist
        hist_cumul.Scale( 1./hist_cumul.Integral() )
        hist_cumul = hist_cumul.GetCumulative()
        hists_cumul.append(hist_cumul)

    return hists_cumul



def plotly1D(h1D):

    y_values_ptr = h1D.GetArray()
    y_values = []
    x_values = []

    for i_bin in range( 1, h1D.GetNbinsX() + 1 ):
        y_values.append( y_values_ptr[i_bin] )
        x_values.append( h1D.GetBinCenter(i_bin) )

    #return [ go.Bar(y = y_values) ]
    plotly.offline.iplot( [ go.Bar(y = y_values) ] )

## Distributions for each component of the input vectors

In [4]:
hists = []

# Create and plot input distributions
hists.append( project1D("P1[0]", 100,  -20, 200, "; x; events",            "nP1 == 6") )
hists.append( project1D("P1[1]", 100,  -60,  60, "; y; events",            "nP1 == 6") )
hists.append( project1D("P1[2]", 100, -250, 250, "; z; events",            "nP1 == 6") )
hists.append( project1D("P1[3]", 100, -1.5, 1.5, "; #phi; events",         "nP1 == 6") )
hists.append( project1D("P1[4]", 100, -100, 100, "; q/Pt; events",         "nP1 == 6") )
hists.append( project1D("P1[5]", 100,   -5,   5, "; tan(#Lambda); events", "nP1 == 6") )

canvases = drawOnCanvases(hists)

## Correlation between the corresponding components of the input vectors

In [5]:
hists = []

# Create and plot input distributions
hists.append( project2D("P1[0]:P2[0]", 200,  -20, 200, 200,  -20, 200, "; P2[x]; P1[x];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[1]:P2[1]", 200,  -60,  60, 200,  -60,  60, "; P2[y]; P1[y];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[2]:P2[2]", 200, -250, 250, 200, -250, 250, "; P2[z]; P1[z];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[3]:P2[3]", 200, -1.5, 1.5, 200, -1.5, 1.5, "; P2[#phi]; P1[#phi];",                 "nP1 == 6", "colz logz") )
hists.append( project2D("P1[4]:P2[4]", 200, -100, 100, 200, -100, 100, "; P2[q/Pt]; P1[q/Pt];",                 "nP1 == 6", "colz logz") )
hists.append( project2D("P1[5]:P2[5]", 200,   -5,   5, 200,   -5,   5, "; P2[tan(#Lambda)]; P1[tan(#Lambda)];", "nP1 == 6", "colz logz") )

canvases = drawOnCanvases(hists)

## Correlation between the corresponding components of the input and output vectors

In [6]:
hists = []

# Create and plot input distributions
hists.append( project2D("P1[0]:PJ[0]", 200,  -20, 200, 200,  -20, 200, "; PJ[x]; P1[x];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[1]:PJ[1]", 200,  -60,  60, 200,  -60,  60, "; PJ[y]; P1[y];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[2]:PJ[2]", 200, -250, 250, 200, -250, 250, "; PJ[z]; P1[z];",                       "nP1 == 6", "colz logz") )
hists.append( project2D("P1[3]:PJ[3]", 200, -1.5, 1.5, 200, -1.5, 1.5, "; PJ[#phi]; P1[#phi];",                 "nP1 == 6", "colz logz") )
hists.append( project2D("P1[4]:PJ[4]", 200, -100, 100, 200, -100, 100, "; PJ[q/Pt]; P1[q/Pt];",                 "nP1 == 6", "colz logz") )
hists.append( project2D("P1[5]:PJ[5]", 200,   -5,   5, 200,   -5,   5, "; PJ[tan(#Lambda)]; P1[tan(#Lambda)];", "nP1 == 6", "colz logz") )

canvases = drawOnCanvases(hists)

## Difference between individual components in input and output vectors

In [7]:
hists = []

hists.append( project1D("fabs(P2[0] - PJ[0]) / sqrt(E2[1])",  50, 0, 10, "; #chi[x]; prob."           , "nP2 == 6") )
hists.append( project1D("fabs(P2[1] - PJ[1]) / sqrt(E2[2])",  50, 0, 10, "; #chi[y]; prob."           , "nP2 == 6") )
hists.append( project1D("fabs(P2[2] - PJ[2]) / sqrt(E2[5])",  50, 0, 10, "; #chi[z]; prob."           , "nP2 == 6") )
hists.append( project1D("fabs(P2[3] - PJ[3]) / sqrt(E2[9])",  50, 0, 10, "; #chi[#phi]; prob."        , "nP2 == 6") )
hists.append( project1D("fabs(P2[4] - PJ[4]) / sqrt(E2[14])", 50, 0, 10, "; #chi[q/Pt]; prob."        , "nP2 == 6") )
hists.append( project1D("fabs(P2[5] - PJ[5]) / sqrt(E2[20])", 50, 0, 10, "; #chi[tan(#Lambda)]; prob.", "nP2 == 6") )

#canvases = drawOnCanvases(hists)
hists_cumul = getCumulative(hists)
canvases = drawOnCanvases(hists_cumul)

## Difference between input and output vectors for all/inner/outer nodes

In [8]:
diff_P2_PJ_chi2 = (
  " (P2[1] - PJ[1]) * (P2[1] - PJ[1]) / E2[2]  + "
  " (P2[2] - PJ[2]) * (P2[2] - PJ[2]) / E2[5]  + "
  " (P2[3] - PJ[3]) * (P2[3] - PJ[3]) / E2[9]  + "
  " (P2[4] - PJ[4]) * (P2[4] - PJ[4]) / E2[14] + "
  " (P2[5] - PJ[5]) * (P2[5] - PJ[5]) / E2[20]   "
)

hists = []

hists.append( project1D(diff_P2_PJ_chi2, 50, 0, 50, "; #chi^2; ", "nP1 == 6") )
hists.append( project1D(diff_P2_PJ_chi2, 50, 0, 50, "; #chi^2; ", "nP1 == 6 && ino == 1") )
hists.append( project1D(diff_P2_PJ_chi2, 50, 0, 50, "; #chi^2; ", "nP1 == 6 && ino == -1") )

hists_cumul = getCumulative(hists)
canvases = drawOnCanvases(hists_cumul)

## Auxilary plots

1 nP2 vs nP1
2 inner/middle/outer = -1/0/1. More outer nodes than inner ones?
3 Direction of the fit. The fit is done only in one direction (0 = outside in)

In [9]:
hists = []

hists.append( project2D("nP2:nP1", 10, 0, 10, 10, 0, 10, "; nP1; nP2", "", "colz") )
hists.append( project1D("ino", 5, -2, 3, "; inner/middle/outer; ", "nP1 == 6") )
hists.append( project1D("dir", 4, -2, 2, "; fit direction; ", "") )
hists.append( project1D("dir", 4, -2, 2, "; fit direction; ", "nP1 == 6") )

canvases = drawOnCanvases(hists)

The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.